In [1]:
!pip install altair vega_datasets pandas


In [2]:
import pandas as pd
import altair as alt
from vega_datasets import data


In [6]:

# Load the dataset from the provided URL
url = "https://raw.githubusercontent.com/UIUC-iSchool-DataViz/is445_data/main/building_inventory.csv"
data = pd.read_csv(url)
data.head()



Agency Name  \
0  Department of Natural Resources   
1  Department of Natural Resources   
2  Department of Natural Resources   
3  Department of Natural Resources   
4  Department of Natural Resources   

                                     Location Name             Address  \
0  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
1  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
2  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
3  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
4  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   

      City  Zip code  County  Congress Dist Congressional Full Name  Rep Dist  \
0  Astoria     61501  Fulton             17            Cheri Bustos        93   
1  Astoria     61501  Fulton             17            Cheri Bustos        93   
2  Astoria     61501  Fulton             17            Cheri Bustos        93   
3  Astoria     61501  Fulton             17            Cheri Bustos        93   
4  Astoria     61501  Fulton             17            Cheri Bustos        93   

       Rep Full Name  ...  Bldg Status Year Acquired Year Constructed  \
0  Hammond Norine K.  ...       In Use          1975             1975   
1  Hammond Norine K.  ...       In Use          2004             2004   
2  Hammond Norine K.  ...       In Use          2004             2004   
3  Hammond Norine K.  ...       In Use          2004             2004   
4  Hammond Norine K.  ...       In Use          2004             2004   

   Square Footage  Total Floors  Floors Above Grade  Floors Below Grade  \
0             144             1                   1                   0   
1             144             1                   1                   0   
2             144             1                   1                   0   
3             144             1                   1                   0   
4             144             1                   1                   0   

   Usage Description  Usage Description 2 Usage Description 3  
0            Unusual              Unusual        Not provided  
1            Unusual              Unusual        Not provided  
2            Unusual              Unusual        Not provided  
3            Unusual              Unusual        Not provided  
4            Unusual              Unusual        Not provided  

[5 rows x 22 columns]

In [10]:
data_cleaned = data.dropna(subset=['Year Constructed', 'Total Floors', 'Square Footage'])
data_cleaned['Year Constructed'] = data_cleaned['Year Constructed'].astype(str)
data_cleaned.head()


Agency Name  \
0  Department of Natural Resources   
1  Department of Natural Resources   
2  Department of Natural Resources   
3  Department of Natural Resources   
4  Department of Natural Resources   

                                     Location Name             Address  \
0  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
1  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
2  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
3  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   
4  Anderson Lake Conservation Area - Fulton County  Anderson Lake C.a.   

      City  Zip code  County  Congress Dist Congressional Full Name  Rep Dist  \
0  Astoria     61501  Fulton             17            Cheri Bustos        93   
1  Astoria     61501  Fulton             17            Cheri Bustos        93   
2  Astoria     61501  Fulton             17            Cheri Bustos        93   
3  Astoria     61501  Fulton             17            Cheri Bustos        93   
4  Astoria     61501  Fulton             17            Cheri Bustos        93   

       Rep Full Name  ...  Bldg Status Year Acquired Year Constructed  \
0  Hammond Norine K.  ...       In Use          1975             1975   
1  Hammond Norine K.  ...       In Use          2004             2004   
2  Hammond Norine K.  ...       In Use          2004             2004   
3  Hammond Norine K.  ...       In Use          2004             2004   
4  Hammond Norine K.  ...       In Use          2004             2004   

   Square Footage Total Floors  Floors Above Grade  Floors Below Grade  \
0             144            1                   1                   0   
1             144            1                   1                   0   
2             144            1                   1                   0   
3             144            1                   1                   0   
4             144            1                   1                   0   

   Usage Description  Usage Description 2 Usage Description 3  
0            Unusual              Unusual        Not provided  
1            Unusual              Unusual        Not provided  
2            Unusual              Unusual        Not provided  
3            Unusual              Unusual        Not provided  
4            Unusual              Unusual        Not provided  

[5 rows x 22 columns]

In [12]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [17]:
data_cleaned['Square Footage'] = pd.to_numeric(data_cleaned['Square Footage'], errors='coerce')

data_cleaned['Total Floors'] = pd.to_numeric(data_cleaned['Total Floors'], errors='coerce')

data_cleaned['Year Constructed'] = data_cleaned['Year Constructed'].astype(str)



Agency Name                object
Location Name              object
Address                    object
City                       object
Zip code                    int64
County                     object
Congress Dist               int64
Congressional Full Name    object
Rep Dist                    int64
Rep Full Name              object
Senate Dist                 int64
Senator Full Name          object
Bldg Status                object
Year Acquired               int64
Year Constructed           object
Square Footage              int64
Total Floors                int64
Floors Above Grade          int64
Floors Below Grade          int64
Usage Description          object
Usage Description 2        object
Usage Description 3        object
Suare Footage               int64
dtype: object

In [50]:
import os

os.makedirs('charts', exist_ok=True)

In [54]:
# Define a selection for highlighting data points based on 'Year Constructed'
highlight = alt.selection_point(
    fields=['Year Constructed'],
    bind='legend',
    name="Highlight Year"
)

chart1 = alt.Chart(data_cleaned).mark_circle().encode(
    x='Square Footage:Q',
    y='Total Floors:O',
    tooltip=['Square Footage', 'Total Floors', 'Year Constructed'],
    size= alt.condition(highlight, alt.value(300), alt.value(80)),
    color= alt.Color('Year Constructed:N', scale=alt.Scale(scheme='category10')),
    opacity=alt.condition(highlight, alt.value(1), alt.value(0.5)),
).properties(
    title="Building Size vs. Number of Stories (Interactive)",
    width=800,
    height=600
).add_params(
    highlight
).interactive()
chart1.save("charts/chart1.html")
chart1


alt.Chart(...)

In [55]:

data_aggregated = data_cleaned.groupby('Total Floors')['Square Footage'].mean().reset_index()

brush = alt.selection_interval(encodings=['x', 'y'])

chart2 = alt.Chart(data_aggregated).mark_bar().encode(
    x='Total Floors:O',
    y='Square Footage:Q',
    color='Total Floors:N',
    tooltip=['Total Floors', 'Square Footage']
).properties(
    title="Average Building Size by Number of Stories"
).add_params(
    brush
).interactive()
chart2.save("charts/chart2.html")
chart2


alt.Chart(...)